# Cryptocurrency Indicators

### Indicadores del Bitcoin

"Projecto" : "Análisis_criptomonedas"  
"Título" : "Indicadores del Bitcoin"  
"Autor" : "Cristian García Díaz"  
"Fecha de creación" : "20180616"  
"Fecha de modificación" : "20180626"  
"Fuentes":  
>https://www.quandl.com/collections/markets/bitcoin-data

## Índice
[1. Configuración del entorno y obtención de los datos](#1)  
[2. Indicadores del mercado Bitcoin](#2)  
[3. Correlación de los indicadores de Bitcoin](#3)  
[4. Obtención y análisis del volumen cambio entre *Bitcoin* y divisas](#4) 

## <a name="1"></a> 1. Configuración del entorno y obtención de los datos

   - Instalar Anaconda.  
   - Instalar las librerias, dependencias y paquetes necesarios.  
   - Crear un entorno de trabajo.
   - Estructura de carpetas para almacenar los datos.  
   - Configuración de la API Key.  
   - Función para obtención de datos desde las APIs. 

In [2]:
# Se importan las líbrerias, dependencias o paquetes necesarios
import numpy as np
import pandas as pd
import pickle
import quandl
from datetime import datetime
import plotly as py
import os

In [3]:
# Se importa el paquete Plotly
import plotly.offline as py
import plotly.graph_objs as go
import plotly.figure_factory as ff
# Se configura el modo offline
py.init_notebook_mode(connected=True)

In [4]:
# API Key Quandl
quandl.ApiConfig.api_key = "gjodR_eNGkrTQq24cufg"

In [5]:
# Comprobar si no esta creada la carpeta de archivos para almacenar los datos
if not os.path.exists("cryptocurrency_indicators_files"):
    os.mkdir('cryptocurrency_indicators_files')

In [6]:
# Se define una función Quandl para cargar los datos
"""pickle --> para no descargar de nuevo los mismo datos"""
"""La función devuelve un Dataframe Pandas"""

def get_quandl_data(quandl_id):
    """Descargamos en cache los datos de Quandl"""
    """Se almacena un fichero .pkl como cache de los datos"""
    cache_path='.\cryptocurrency_indicators_files\{}.pkl'.format(quandl_id).replace('/','-')
    try:
        f = open(cache_path,'rb')
        df = pickle.load(f)
        print('Dataset {} cargado del cache'.format(quandl_id))
    except (OSError,IOError)as e:
        print('Descargando {} de Quandl'.format(quandl_id))
        df = quandl.get(quandl_id, returns="pandas")
        df.to_pickle(cache_path)
        print('Cargado {} de {} en el cache'.format(quandl_id,cache_path))
    return df

In [7]:
# Se define la función para visualizar los datos
def df_scatter(df, title,seperate_y_axis=False, y_axis_label='',scale='linear',initial_hide=False):
    # Se definen la lista de los nombres de cada dataframe como una lista label_arr = ['BITSTAMP', 'COINBASE', 'ITBIT', 'KRAKEN']
    label_arr = list(df)
    # Aplicamos una función lambda para mapear cada columnas y asignar la etiqueta correspondiente
    # Se guarda como otra lista series_arr
    series_arr = list(map(lambda col:df[col],label_arr))
    
    # Se definen los parametros de la salida gráfica
    layout = go.Layout(
        title = title,
        legend = dict(orientation='h'),
        xaxis = dict(type='date'),
        yaxis = dict(
            title = y_axis_label, 
            showticklabels = not seperate_y_axis,
            type = scale
        )
    )
    
    # Se define la configuración del eje y
    y_axis_config = dict(
        overlaying = 'y',
        showticklabels = False,
        type = scale
    )
    
    # Se define la visibilidad
    visibility = 'visible'
    if initial_hide:
        visibility = 'legendonly'
        
    # Se define la forma para cada serie de datos
    trace_arr = []
    for index, series in enumerate(series_arr):
        trace = go.Scatter(
        x = series.index,
        y = series,
        name = label_arr[index],
        visible = visibility
        )
        
        #Añadir un eje separado para cada serie
        if seperate_y_axis:
            trace['yaxis'] = 'y{format}'.format(index + 1)
            layout['yaxis{}'.format(index + 1)] = y_axis_config
        trace_arr.append(trace)
    
    fig = go.Figure(data = trace_arr, layout = layout)
    py.iplot(fig)

## <a name="2"></a> 2. Indicadores del mercado Bitcoin
   - [2.1 Precio de Bitcoin](#2.1)
   - [2.2 Número total de bictoins](#2.2)
   - [2.3 Valor del mercado](#2.3) 
   - [2.4 Direcciones de bitcoin](#2.4) 
   - [2.5 Volumen de cambio de bitcoin a dóladores](#2.5) 
   - [2.6 Número de transacciones de bitcoin](#2.6) 
   - [2.7 Número de transacciones acumuladas de bitcoin](#2.7) 
   - [2.8 Hash rate de bitcoin](#2.8) 
   - [2.9 Dificultad de bitcoin](#2.9) 
   - [2.10 Recompensa de los mineros de bitcoin](#2.10) 
   
   "Fuentes":  
>https://www.quandl.com/data/BCHAIN-Blockchain

### <a name="2.1"></a> 2.1 Precio de Bitcoin

In [8]:
# Obtención de los datos del precio
price_btc = get_quandl_data("BCHAIN/MKPRU")

Dataset BCHAIN/MKPRU cargado del cache


In [9]:
# Gráfico del número total de Bitcoins
price_btc_graphic = go.Scatter(x=price_btc.index,y=price_btc['Value'])
py.iplot([price_btc_graphic])

In [10]:
# Gráfico del número total de Bitcoins
df_scatter(price_btc,"Precio medio de Bitcoin (USD)")

### <a name="2.2"></a> 2.2 Número total de bictoins

In [11]:
# Se obtienen los datos históricos del número total de Bitcoins
total_number_btc = get_quandl_data("BCHAIN/TOTBC")

Dataset BCHAIN/TOTBC cargado del cache


In [12]:
# Número total máximo de Bitcoin y fecha
max_number_btc_date = total_number_btc.index.max().strftime('%Y-%m-%d')
print(max_number_btc_date)
max_number_btc = total_number_btc.Value.max()
print("{:.0f}".format(max_number_btc))

2018-08-26
17230712


In [13]:
# Información del número de bitcoins totales
max_total_number_btc = "El número máximo de Bitcoins del dia {} es de {:.0f}".format(max_number_btc_date,max_number_btc)
print(max_total_number_btc)

El número máximo de Bitcoins del dia 2018-08-26 es de 17230712


In [14]:
# Gráfico del número total de Bitcoins
total_number_btc_graphic = go.Scatter(x=total_number_btc.index, y=total_number_btc.Value)
py.iplot([total_number_btc_graphic])

### <a name="2.3"></a> 2.3 Valor del mercado

In [15]:
# Se obtienen los datos históricos de la capitalización del mercado del Bitcoin en USD. El valor de mercado del Bitcoin
market_capitalization_btc = get_quandl_data("BCHAIN/MKTCP")

Dataset BCHAIN/MKTCP cargado del cache


In [16]:
# Capitalización máxima del mercado del bitcoin
max_capitalization_btc=market_capitalization_btc[market_capitalization_btc.Value == market_capitalization_btc['Value'].max()]

In [17]:
# Fecha y valor de la capitalización máxima del mercado del bitcoin
max_capitalization_btc_date = max_capitalization_btc.index.max().strftime('%Y-%m-%d')
print(max_capitalization_btc_date)
max_capitalization_btc_number = max_capitalization_btc.Value.max()
print("{:,}".format(max_capitalization_btc_number))
print("{:.0f}".format(max_capitalization_btc_number))

2017-12-17
326,525,438,567.0
326525438567


In [18]:
# Información de la capitalización máxima del bitcoin
max_market_capitalization_btc = "La máxima capitalización del mercado Bitcoin es del dia {} con un total de {:,} USD".format(max_capitalization_btc_date,max_capitalization_btc_number)
print(max_market_capitalization_btc)

La máxima capitalización del mercado Bitcoin es del dia 2017-12-17 con un total de 326,525,438,567.0 USD


In [19]:
# Gráfico de la capitalización del mercado del bitcoin
capitalization_btc_graphic = go.Scatter(x=market_capitalization_btc.index, y=market_capitalization_btc.Value)
py.iplot([capitalization_btc_graphic])

### <a name="2.4"></a> 2.4 Número de direcciones bitcoin

In [20]:
# Se obtienen los datos históricos del número de direcciones Bitcoin usadas por dia
address_btc = get_quandl_data("BCHAIN/NADDU")

Dataset BCHAIN/NADDU cargado del cache


In [21]:
# Máximo de direcciones únicas de bitcoin utilizadas por dia
max_address_btc = address_btc[address_btc.Value == address_btc['Value'].max()]

In [22]:
# Fecha y valor del número máximo de direcciones únicas de bitcoin
max_address_btc_date = max_address_btc.index.max().strftime('%Y-%m-%d')
print(max_address_btc_date)
max_address_btc_number = max_address_btc.Value.max()
print("{:,}".format(max_address_btc_number))
print("{:.0f}".format(max_address_btc_number))

2017-12-15
1,072,861.0
1072861


In [23]:
# Información del número máximo de direcciones del bitcoin
max_address_btc = "El número máximo de direcciones únicas de Bitcoin es del dia {} con un total de {:,} direcciones".format(max_address_btc_date,max_address_btc_number)
print(max_address_btc)

El número máximo de direcciones únicas de Bitcoin es del dia 2017-12-15 con un total de 1,072,861.0 direcciones


In [24]:
# Gráfico de las direcciones únicas de bitcoin utilizadas por dia
number_address_btc_graphic = go.Scatter(x=address_btc.index, y=address_btc.Value)
py.iplot([number_address_btc_graphic])

### <a name="2.5"></a> 2.5 Volumen de cambio de USD/BTC

In [25]:
# Se obtienen los datos históricos del volumen de cambio USD/BTC
exchange_trade_btc = get_quandl_data("BCHAIN/TRVOU")

Dataset BCHAIN/TRVOU cargado del cache


In [26]:
# Máximo de volumen de cambio USD/BTC
max_exchange_trade_btc = exchange_trade_btc [exchange_trade_btc .Value == exchange_trade_btc ['Value'].max()]

In [27]:
# Fecha y valor del número máximo de cambio USD/BTC
max_exchange_trade_btc_date = max_exchange_trade_btc.index.max().strftime('%Y-%m-%d')
print(max_exchange_trade_btc_date)
max_exchange_trade_btc_number = max_exchange_trade_btc.Value.max()
print("{:,}".format(max_exchange_trade_btc_number))
print("{:.0f}".format(max_exchange_trade_btc_number))

2017-12-23
5,352,015,515.54
5352015516


In [28]:
# Información del volumen máximo de cambio USD/BTC
max_exchange_trade_btc = "El volumen máximo de de cambio USD/BTC es del dia {} con un total de {:,} cambios USD/BTC".format(max_exchange_trade_btc_date,max_exchange_trade_btc_number)
print(max_exchange_trade_btc)

El volumen máximo de de cambio USD/BTC es del dia 2017-12-23 con un total de 5,352,015,515.54 cambios USD/BTC


In [29]:
# Gráfico del volumen de cambio USD/BTC
number_exchange_trade_btc_graphic = go.Scatter(x=exchange_trade_btc.index, y=exchange_trade_btc.Value)
py.iplot([number_exchange_trade_btc_graphic])

### <a name="2.6"></a> 2.6 Número de transacciones Bitcoin

In [30]:
# Se obtienen los datos históricos de las transacciones de BTC
transactions_btc = get_quandl_data("BCHAIN/NTRAN")

Dataset BCHAIN/NTRAN cargado del cache


In [31]:
# Máximo de volumen transacciones de BTC
max_transactions_btc = transactions_btc [transactions_btc .Value == transactions_btc ['Value'].max()]

In [32]:
# Fecha y valor del número máximo de transacciones de BTC
max_transactions_btc_date = max_transactions_btc.index.max().strftime('%Y-%m-%d')
print(max_transactions_btc_date)
max_transactions_btc_number = max_transactions_btc.Value.max()
print("{:,}".format(max_transactions_btc_number))
print("{:.0f}".format(max_transactions_btc_number))

2017-12-15
490,644.0
490644


In [33]:
# Información del volumen máximo transacciones de BTC
max_transactions_btc = "El volumen máximo de de cambio USD/BTC es del dia {} con un total de {:,} cambios USD/BTC".format(max_transactions_btc_date,max_transactions_btc_number)
print(max_transactions_btc)

El volumen máximo de de cambio USD/BTC es del dia 2017-12-15 con un total de 490,644.0 cambios USD/BTC


In [34]:
# Gráfico del volumen de cambio USD/BTC
number_transactions_btc_graphic = go.Scatter(x=transactions_btc.index, y=transactions_btc.Value)
py.iplot([number_transactions_btc_graphic])

### <a name="2.7"></a> 2.7 Número de transacciones acumuladas Bitcoin

In [35]:
# Se calculan el volumen de cambio USD/BTC acumulativo con la función cumsum()
transactions_btc_acumulative = transactions_btc.cumsum()

In [36]:
# Gráfico del volumen del volumen de cambio USD/BTC acumulativo
transactions_btc_acumulative_graphic = go.Scatter(x=transactions_btc_acumulative.index, y=transactions_btc_acumulative.Value)
py.iplot([transactions_btc_acumulative_graphic])

### <a name="2.8"></a> 2.8 Hash rate de bitcoin 

In [37]:
# Se obtienen los datos históricos de Hash rate de bitcoin
# Es el número estimado de hash rate de Bitcoun y se miden en TeraHashes por segundo TH/s.
# 1 TH/s = 10^12 = 1.000.000.000.000 hash/s = 1 billón de hashes por segundo.
hash_rate_btc = get_quandl_data("BCHAIN/HRATE")

Dataset BCHAIN/HRATE cargado del cache


In [38]:
# Gráfico del hash rate de Bitcoin
hash_rate_btc_graphic = go.Scatter(x=hash_rate_btc.index, y=hash_rate_btc.Value)
py.iplot([hash_rate_btc_graphic])

### <a name="2.9"></a> 2.9 Dificultad de bitcoin

In [39]:
# Se obtienen la dificultad de Bitcoin. Es una medida de dificultad propia.
# cada 210.000 bloques se recalcula la dificultad para crear bloques en la cadena de bloques cada 10 minutos de media.
difficulty_btc = get_quandl_data("BCHAIN/DIFF")

Dataset BCHAIN/DIFF cargado del cache


In [40]:
# Gráfico de la dificultad de Bitcoin
difficulty_btc_graphic = go.Scatter(x=difficulty_btc.index, y=difficulty_btc.Value)
py.iplot([difficulty_btc_graphic])

### <a name="2.10"></a> 2.10 Recompensa de los mineros de bitcoin 

In [41]:
# Se obtienen los datos históricos de la recompensa de los mineros
miners_revenue_btc = get_quandl_data("BCHAIN/MIREV")

Dataset BCHAIN/MIREV cargado del cache


In [42]:
# Gráfico de la recompensa de los mineros
miners_revenue_btc_graphic = go.Scatter(x=miners_revenue_btc.index, y=miners_revenue_btc.Value)
py.iplot([miners_revenue_btc_graphic])

### <a name="2.10"></a> 2.11 Recompensa vs Dificultad

In [43]:
# Dificultad entre recompensa de los mineros.
revenue_vs_diff_btc = difficulty_btc
print(revenue_vs_diff_btc.count())
print(miners_revenue_btc.count())
if revenue_vs_diff_btc.size != miners_revenue_btc.size:
    revenue_vs_diff_btc = revenue_vs_diff_btc.drop(revenue_vs_diff_btc.index[len(revenue_vs_diff_btc)-1])
print(revenue_vs_diff_btc.count())
print(miners_revenue_btc.count())

Value    3523
dtype: int64
Value    3522
dtype: int64
Value    3522
dtype: int64
Value    3522
dtype: int64


In [44]:
revenue_vs_diff_btc.tail()

Value
Date                    
2018-08-21  6.389317e+12
2018-08-22  6.389317e+12
2018-08-23  6.389317e+12
2018-08-24  6.389317e+12
2018-08-25  6.505039e+12

In [45]:
# Cruzar los datos de dificultad vs recompensa
for i in range (len(revenue_vs_diff_btc-1)):
    revenue_vs_diff_btc.iloc[i] = miners_revenue_btc.iloc[i]/revenue_vs_diff_btc.iloc[i]

In [46]:
# Gráfico de los datos de dificultad vs recompensa
revenue_vs_diff_btc_graphic = go.Scatter(x=revenue_vs_diff_btc.index, y=revenue_vs_diff_btc.Value)
py.iplot([revenue_vs_diff_btc_graphic])

## <a name="3"></a>3. Correlación de los indicadores de Bitcoin

In [47]:
# Se preparan los datos para unirlos en un único Dataframe para poder aplicar la correlación.
mesures_name= ["price_btc",
        "total_number_btc",
        "market_capitalization_btc",
        "address_btc",
        "exchange_trade_btc",
        "transactions_btc",
        "transactions_btc_acumulative",
        "hash_rate_btc",
        "difficulty_btc",
        "miners_revenue_btc"]

mesures_data= [price_btc,
        total_number_btc,
        market_capitalization_btc,
        address_btc,
        exchange_trade_btc,
        transactions_btc,
        transactions_btc_acumulative,
        hash_rate_btc,
        difficulty_btc,
        miners_revenue_btc]

In [48]:
# Preparación de un Dataframe con todos los indicadores e igualar los días para construir para todos los indicadores
fecha=pd.Timestamp(2018, 8, 26)

for i in range(len(mesures_name)):
    if(mesures_data[i].index.max()== fecha):
        mesures_data[i] = mesures_data[i].drop(mesures_data[i].index[len(mesures_data[i])-1])
    print( i, mesures_name[i], mesures_data[i].index.max()-mesures_data[i].index.min(), mesures_data[i].index.max())

0 price_btc 3521 days 00:00:00 2018-08-25 00:00:00
1 total_number_btc 3521 days 00:00:00 2018-08-25 00:00:00
2 market_capitalization_btc 3521 days 00:00:00 2018-08-25 00:00:00
3 address_btc 3521 days 00:00:00 2018-08-25 00:00:00
4 exchange_trade_btc 3521 days 00:00:00 2018-08-25 00:00:00
5 transactions_btc 3521 days 00:00:00 2018-08-25 00:00:00
6 transactions_btc_acumulative 3521 days 00:00:00 2018-08-25 00:00:00
7 hash_rate_btc 3520 days 00:00:00 2018-08-25 00:00:00
8 difficulty_btc 3521 days 00:00:00 2018-08-25 00:00:00
9 miners_revenue_btc 3521 days 00:00:00 2018-08-25 00:00:00


In [49]:
# Se realiza una unión de los varios Dataframe en uno
mesures_bitcoin = pd.concat(
    [mesures_data[0],
     mesures_data[1],
     mesures_data[2],
     mesures_data[3],
     mesures_data[4],
     mesures_data[5],
     mesures_data[6],
     mesures_data[7],
     mesures_data[8],
     mesures_data[9]],axis=1
)

In [50]:
# Renombrar las columnas
for i in range(len(mesures_name)):
    mesures_bitcoin.columns.values[i] = mesures_name[i]

In [51]:
mesures_bitcoin.tail()

price_btc  total_number_btc  market_capitalization_btc  \
Date                                                                   
2018-08-21  6434.559167        17221487.5               1.108127e+11   
2018-08-22  6401.246154        17223337.5               1.102508e+11   
2018-08-23  6575.229167        17225337.5               1.132605e+11   
2018-08-24  6434.881667        17227200.0               1.108550e+11   
2018-08-25  6543.645714        17229025.0               1.127406e+11   

            address_btc  exchange_trade_btc  transactions_btc  \
Date                                                            
2018-08-21     459855.0        2.784076e+08          214983.0   
2018-08-22     449915.0        4.942757e+08          217777.0   
2018-08-23     484462.0        5.786947e+08          230333.0   
2018-08-24     444345.0        5.214981e+08          217352.0   
2018-08-25     487990.0        3.094877e+08          219848.0   

            transactions_btc_acumulative  hash_rate_btc  difficulty_btc  \
Date                                                                      
2018-08-21                   336282533.0   4.764220e+07    6.389317e+12   
2018-08-22                   336500310.0   4.700697e+07    6.389317e+12   
2018-08-23                   336730643.0   5.081835e+07    6.389317e+12   
2018-08-24                   336947995.0   4.732459e+07    6.389317e+12   
2018-08-25                   337167843.0   4.882418e+07    6.505039e+12   

            miners_revenue_btc  
Date                            
2018-08-21        1.225187e+07  
2018-08-22        1.200075e+07  
2018-08-23        1.331007e+07  
2018-08-24        1.210921e+07  
2018-08-25        1.206749e+07

In [52]:
# Correlación de las variables
mesures_correlacion = mesures_bitcoin.corr()

In [72]:
# Correlación entre las variables
mesures_correlacion

price_btc  total_number_btc  \
price_btc                      1.000000          0.465134   
total_number_btc               0.465134          1.000000   
market_capitalization_btc      0.999782          0.458457   
address_btc                    0.677478          0.808610   
exchange_trade_btc             0.853488          0.342171   
transactions_btc               0.582283          0.818690   
transactions_btc_acumulative   0.794963          0.750328   
hash_rate_btc                  0.779903          0.420175   
difficulty_btc                 0.775728          0.421509   
miners_revenue_btc             0.980981          0.457854   

                              market_capitalization_btc  address_btc  \
price_btc                                      0.999782     0.677478   
total_number_btc                               0.458457     0.808610   
market_capitalization_btc                      1.000000     0.672858   
address_btc                                    0.672858     1.000000   
exchange_trade_btc                             0.852266     0.568590   
transactions_btc                               0.577893     0.983264   
transactions_btc_acumulative                   0.794873     0.913800   
hash_rate_btc                                  0.786708     0.514078   
difficulty_btc                                 0.782611     0.511148   
miners_revenue_btc                             0.978755     0.674568   

                              exchange_trade_btc  transactions_btc  \
price_btc                               0.853488          0.582283   
total_number_btc                        0.342171          0.818690   
market_capitalization_btc               0.852266          0.577893   
address_btc                             0.568590          0.983264   
exchange_trade_btc                      1.000000          0.482211   
transactions_btc                        0.482211          1.000000   
transactions_btc_acumulative            0.610836          0.880171   
hash_rate_btc                           0.560481          0.449453   
difficulty_btc                          0.554420          0.446921   
miners_revenue_btc                      0.865675          0.577882   

                              transactions_btc_acumulative  hash_rate_btc  \
price_btc                                         0.794963       0.779903   
total_number_btc                                  0.750328       0.420175   
market_capitalization_btc                         0.794873       0.786708   
address_btc                                       0.913800       0.514078   
exchange_trade_btc                                0.610836       0.560481   
transactions_btc                                  0.880171       0.449453   
transactions_btc_acumulative                      1.000000       0.776283   
hash_rate_btc                                     0.776283       1.000000   
difficulty_btc                                    0.778200       0.994816   
miners_revenue_btc                                0.738364       0.698855   

                              difficulty_btc  miners_revenue_btc  
price_btc                           0.775728            0.980981  
total_number_btc                    0.421509            0.457854  
market_capitalization_btc           0.782611            0.978755  
address_btc                         0.511148            0.674568  
exchange_trade_btc                  0.554420            0.865675  
transactions_btc                    0.446921            0.577882  
transactions_btc_acumulative        0.778200            0.738364  
hash_rate_btc                       0.994816            0.698855  
difficulty_btc                      1.000000            0.685947  
miners_revenue_btc                  0.685947            1.000000

In [54]:
# Correlación entre las variables
mesures_correlacion['price_btc'].sort_values(ascending=False)

price_btc                       1.000000
market_capitalization_btc       0.999782
miners_revenue_btc              0.980981
exchange_trade_btc              0.853488
transactions_btc_acumulative    0.794963
hash_rate_btc                   0.779903
difficulty_btc                  0.775728
address_btc                     0.677478
transactions_btc                0.582283
total_number_btc                0.465134
Name: price_btc, dtype: float64

In [64]:
# Corelación sin tener en cuenta variable de market_capitalization_btc, transactions_btc_acumulative
# miners_revenue_btc y difficulty_btc 
mesures_bitcoin_2 = mesures_bitcoin.drop(columns=['market_capitalization_btc','transactions_btc_acumulative','miners_revenue_btc','difficulty_btc'])

In [65]:
# Correlación
mesures_correlacion_2 = mesures_bitcoin_2.corr()

In [66]:
mesures_correlacion_2

price_btc  total_number_btc  address_btc  \
price_btc            1.000000          0.465134     0.677478   
total_number_btc     0.465134          1.000000     0.808610   
address_btc          0.677478          0.808610     1.000000   
exchange_trade_btc   0.853488          0.342171     0.568590   
transactions_btc     0.582283          0.818690     0.983264   
hash_rate_btc        0.779903          0.420175     0.514078   

                    exchange_trade_btc  transactions_btc  hash_rate_btc  
price_btc                     0.853488          0.582283       0.779903  
total_number_btc              0.342171          0.818690       0.420175  
address_btc                   0.568590          0.983264       0.514078  
exchange_trade_btc            1.000000          0.482211       0.560481  
transactions_btc              0.482211          1.000000       0.449453  
hash_rate_btc                 0.560481          0.449453       1.000000

In [73]:
# Correlación
mesures_correlacion_3 = mesures_bitcoin_2.pct_change().corr(method='pearson')

In [74]:
mesures_correlacion_3

price_btc  total_number_btc  address_btc  \
price_btc            1.000000          0.079043     0.059871   
total_number_btc     0.079043          1.000000     0.079735   
address_btc          0.059871          0.079735     1.000000   
exchange_trade_btc   0.189712          0.158137     0.139686   
transactions_btc     0.018550          0.067421     0.811862   
hash_rate_btc        0.017413          0.086914     0.873792   

                    exchange_trade_btc  transactions_btc  hash_rate_btc  
price_btc                     0.189712          0.018550       0.017413  
total_number_btc              0.158137          0.067421       0.086914  
address_btc                   0.139686          0.811862       0.873792  
exchange_trade_btc            1.000000          0.057607       0.021074  
transactions_btc              0.057607          1.000000       0.741195  
hash_rate_btc                 0.021074          0.741195       1.000000

In [75]:
# Correlación de las variables
mesures_correlacion_4 = mesures_bitcoin.pct_change().corr(method='pearson')

In [76]:
mesures_correlacion_4

price_btc  total_number_btc  \
price_btc                      1.000000          0.079043   
total_number_btc               0.079043          1.000000   
market_capitalization_btc      0.996503          0.086811   
address_btc                    0.059871          0.079735   
exchange_trade_btc             0.189712          0.158137   
transactions_btc               0.018550          0.067421   
transactions_btc_acumulative   0.043373          0.999902   
hash_rate_btc                  0.017413          0.086914   
difficulty_btc                 0.010426         -0.002903   
miners_revenue_btc             0.498817          0.107886   

                              market_capitalization_btc  address_btc  \
price_btc                                      0.996503     0.059871   
total_number_btc                               0.086811     0.079735   
market_capitalization_btc                      1.000000     0.061120   
address_btc                                    0.061120     1.000000   
exchange_trade_btc                             0.190665     0.139686   
transactions_btc                               0.019716     0.811862   
transactions_btc_acumulative                   0.047076     0.085786   
hash_rate_btc                                  0.018595     0.873792   
difficulty_btc                                 0.011923    -0.010677   
miners_revenue_btc                             0.501531     0.164133   

                              exchange_trade_btc  transactions_btc  \
price_btc                               0.189712          0.018550   
total_number_btc                        0.158137          0.067421   
market_capitalization_btc               0.190665          0.019716   
address_btc                             0.139686          0.811862   
exchange_trade_btc                      1.000000          0.057607   
transactions_btc                        0.057607          1.000000   
transactions_btc_acumulative            0.068891          0.084807   
hash_rate_btc                           0.021074          0.741195   
difficulty_btc                         -0.000110          0.038501   
miners_revenue_btc                      0.121983          0.054415   

                              transactions_btc_acumulative  hash_rate_btc  \
price_btc                                         0.043373       0.017413   
total_number_btc                                  0.999902       0.086914   
market_capitalization_btc                         0.047076       0.018595   
address_btc                                       0.085786       0.873792   
exchange_trade_btc                                0.068891       0.021074   
transactions_btc                                  0.084807       0.741195   
transactions_btc_acumulative                      1.000000       0.085806   
hash_rate_btc                                     0.085806       1.000000   
difficulty_btc                                    0.002080       0.108501   
miners_revenue_btc                                0.006924       0.810919   

                              difficulty_btc  miners_revenue_btc  
price_btc                           0.010426            0.498817  
total_number_btc                   -0.002903            0.107886  
market_capitalization_btc           0.011923            0.501531  
address_btc                        -0.010677            0.164133  
exchange_trade_btc                 -0.000110            0.121983  
transactions_btc                    0.038501            0.054415  
transactions_btc_acumulative        0.002080            0.006924  
hash_rate_btc                       0.108501            0.810919  
difficulty_btc                      1.000000           -0.115992  
miners_revenue_btc                 -0.115992            1.000000

## <a name="4"></a>4. Obtención y análisis del volumen cambio entre *Bitcoin* y divisas
   - Definición de una función para obtener precios de BTC a partir de la [API Cryptocompare](https://www.cryptocompare.com/api/#-api-data-toppairs-).  
   - Recuperar el volumen de cambio de moneda del CCCAGG *(CriptoCompare Current Aggregate)*  


In [ ]:
def get_json_top_data(json_url,now):
    """Descargamos en cache los datos en formato json"""
    cache_path='.\cryptocurrency_indicators_files\{}.pkl'.format(now)
    try:
        f = open(cache_path,'rb')
        df = pickle.load(f)
        print('Dataset {} cargado del cache'.format(json_url))
    except (OSError,IOError) as e:
        print('Descargando datos {} mediante la API Cryptocompare'.format(json_url))
        df = pd.read_json(json_url)
        df.to_pickle(cache_path)
        print('Cargado {} de {} en el cache'.format(json_url,cache_path))
    return df

In [ ]:
# Definimos una función para obtener un array del top de cambio de monedas a criptomonedas. URL=https://www.cryptocompare.com/api/#-api-data-toppairs-
# Se define la función genera las peticiones vía HTTP a PAPI y se llamará a la función get_json_data para guardar los datos obtenidos
top_base_url = 'https://min-api.cryptocompare.com/data/top/pairs?fsym={}&limit={}'
base_coin = 'BTC'
number_limit = 30

def get_crypto_data():
    '''Captura de los datos de criptomonedas de la API cryptocompare'''
    json_url = top_base_url.format(base_coin, number_limit)
    now = datetime.now().strftime('Currency_top_%Y%m%d')
    data_top_df = get_json_top_data(json_url, now)
    return data_top_df

In [ ]:
data_top_df = get_crypto_data()

In [ ]:
# URL de la API con el top de criptomonedas
json_url = top_base_url.format(base_coin, number_limit)
# Se guarda en un dataframe
df_top = pd.read_json(json_url)
# Se guarda la parte Data como un json
df_top_clear = df_top.Data.to_json(orient='values')
# Se lee la parte que hemos exportado
df_top_final = pd.read_json(df_top_clear)

In [ ]:
# Volumen de cambio de criptomonedas a otra moneda 
df_top_final

In [ ]:
# Array de tipo de cambio de criptomonedas
array_top_ratio_change = df_top_final.toSymbol.values
array_top_ratio_change

## 5. Futuras ideas

   - Realizar peticiones en un bucle con diferentes fechas para obtener un histórico de las evoluciones de cada moneda.  
   - Escoger un top de las 10 primeras monedas (USD,EUR,Yenes,etc...) y ver la evolución BTC-Moneda en el tiempo.  
   - Buscar tendencas en el volumen de operaciones. Proporciones de compra/venta.(correlación no significa causalidad)
   - Entrenar un modelos predictivo de aprendizaje automático en los datos para predecir los precios para mañana.Intentarlo con una red neuronal Recurrente (RNN).